In [23]:
import sys
from tqdm import tqdm as tqdm

In [2]:
!pip install anndata
!pip install scanpy

In [24]:
import pandas as pd
import anndata as ad
import numpy as np
from scipy import sparse
from tqdm import tqdm
import scanpy as sc
import matplotlib.pyplot as plt


In [26]:
df = pd.read_csv('data/counts_patient5.csv', index_col=0)

In [27]:
df['subclone'].unique()

array(['1.1.1.1', '1.1.1.2', '1.1.2.1', '1.1.2.2', '1.2.1.1', '1.2.1.2',
       '1.2.2.1', '1.2.2.2', 'healthy.healthy.1.1.1.1',
       'healthy.healthy.1.1.1.2', 'healthy.healthy.1.1.2.1',
       'healthy.healthy.1.1.2.2', 'healthy.healthy.1.2.1.1',
       'healthy.healthy.1.2.1.2', 'healthy.healthy.1.2.2.1',
       'healthy.healthy.1.2.2.2'], dtype=object)

In [28]:
df['subclone'] = df['subclone'].replace(['healthy.healthy.1.1.1.1',
       'healthy.healthy.1.1.1.2', 'healthy.healthy.1.1.2.1',
       'healthy.healthy.1.1.2.2', 'healthy.healthy.1.2.1.1',
       'healthy.healthy.1.2.1.2', 'healthy.healthy.1.2.2.1',
       'healthy.healthy.1.2.2.2'], 'healthy')

In [29]:
df

22848  14  10058  5825  55347  25864  51099  57406  10152  \
cell_id                                                                         
AAACCCAAGCCTTGAT-1      3   1      0     0      0      0      0      0      0   
AAACGAACAACCCGCA-1      8   0      0     0      2      1      2      0      1   
AAAGAACAGCGCCTAC-1      1   0      0     0      0      0      1      0      0   
AAAGAACGTGGCTGAA-1      1   0      0     0      0      0      0      0      0   
AAAGAACTCGGAGTAG-1      2   0      0     0      0      0      0      0      0   
...                   ...  ..    ...   ...    ...    ...    ...    ...    ...   
TTTGTTGGTGCCTGCA-1      6   1      0     1      0      0      2      0      0   
TTTGTTGGTGTAGCAG-1      1   0      0     0      0      0      0      0      0   
TTTGTTGTCGCCAGAC-1      6   0      0     1      0      0      1      0      0   
TTTGTTGTCTGGACCG-1      1   0      0     0      0      1      0      0      0   
TTTGTTGTCTGGGTCG-1      1   0      0     0      0      0      0      0      0   

                    25890  ...  125893  55769  7644  81931  8233  65982  \
cell_id                    ...                                            
AAACCCAAGCCTTGAT-1      0  ...       0      1     1      1     0      0   
AAACGAACAACCCGCA-1      0  ...       0      1     0      0     0      0   
AAAGAACAGCGCCTAC-1      0  ...       0      0     0      0     0      0   
AAAGAACGTGGCTGAA-1      0  ...       0      0     0      0     0      0   
AAAGAACTCGGAGTAG-1      0  ...       0      1     0      0     0      0   
...                   ...  ...     ...    ...   ...    ...   ...    ...   
TTTGTTGGTGCCTGCA-1      0  ...       0      0     0      0     0      0   
TTTGTTGGTGTAGCAG-1      0  ...       0      0     0      0     0      0   
TTTGTTGTCGCCAGAC-1      0  ...       0      0     0      0     0      0   
TTTGTTGTCTGGACCG-1      0  ...       0      1     0      0     0      0   
TTTGTTGTCTGGGTCG-1      0  ...       0      0     0      0     0      0   

                    79149  90204  158586  subclone  
cell_id                                             
AAACCCAAGCCTTGAT-1      0      0       0   1.1.1.1  
AAACGAACAACCCGCA-1      0      0       0   1.1.1.1  
AAAGAACAGCGCCTAC-1      0      0       0   1.1.1.1  
AAAGAACGTGGCTGAA-1      0      0       0   1.1.1.1  
AAAGAACTCGGAGTAG-1      0      0       0   1.1.1.1  
...                   ...    ...     ...       ...  
TTTGTTGGTGCCTGCA-1      2      0       0   1.1.1.1  
TTTGTTGGTGTAGCAG-1      0      0       0   1.1.1.1  
TTTGTTGTCGCCAGAC-1      1      0       0   1.1.1.1  
TTTGTTGTCTGGACCG-1      0      0       0   1.1.1.1  
TTTGTTGTCTGGGTCG-1      0      0       0   1.1.1.1  

[2365 rows x 9609 columns]

In [30]:
np.random.seed(42)

In [34]:
import pandas as pd
import numpy as np
from scipy import sparse

def sum_by_df(df: pd.DataFrame, group_col: str) -> pd.DataFrame:
    """
    Aggregates gene expression counts by group within a single DataFrame.

    Parameters:
    - df: pandas DataFrame. Each row is a cell. 
          Columns are gene expression (numeric), plus one column with group labels.
    - group_col: string. Name of the column that contains group/subclone labels.

    Returns:
    - A DataFrame indexed by group_col, where each row is a group (e.g., subclone) 
      and columns are the summed gene expression features.
    """

    # Ensure group_col exists
    if group_col not in df.columns:
        raise ValueError(f"Group column '{group_col}' not found in dataframe columns")

    # List all gene feature columns (everything except the group column)
    gene_cols = [col for col in df.columns if col != group_col]

    # Ensure group_col is categorical
    df[group_col] = df[group_col].astype('category')
    cat = df[group_col].cat
    n_obs = df.shape[0]

    # Build a sparse indicator matrix for efficient summing
    indicator = sparse.coo_matrix(
        (
            np.ones(n_obs, dtype=bool),
            (cat.codes, np.arange(n_obs))
        ),
        shape=(len(cat.categories), n_obs)
    )

    # Extract and validate gene expression matrix (cells x genes)
    data_matrix = df[gene_cols].values
    if not sparse.issparse(data_matrix):
        data_matrix = sparse.csr_matrix(data_matrix)

    # Matrix multiplication: (groups x cells) @ (cells x genes) = (groups x genes)
    summed = indicator @ data_matrix

    # Output DataFrame, indexed by group, with gene columns
    summed_df = pd.DataFrame(
        summed.toarray(),
        index=cat.categories,
        columns=gene_cols
    )
    summed_df.index.name = group_col

    return summed_df

In [35]:
df['subclone'].unique()

array(['1.1.1.1', '1.1.1.2', '1.1.2.1', '1.1.2.2', '1.2.1.1', '1.2.1.2',
       '1.2.2.1', '1.2.2.2', 'healthy'], dtype=object)

In [36]:
for i in tqdm(range(100)):
    bootstrap_ids = np.random.choice(df.index, size=4000)
    subsampled_df = df.loc[bootstrap_ids]
    bulked = sum_by_df(subsampled_df, 'subclone')
    bulked.to_csv(f'data/pseudobulks/bulked_pat5_iter{i+1}.csv', index=True)

100%|██████████| 100/100 [01:48<00:00,  1.09s/it]


In [37]:
# Define path template for input files
path_template = 'data/pseudobulks/bulked_pat5_iter{}.csv'

# Load the first bulk
i = 0
bulk_df = pd.read_csv(path_template.format(i+1))
bulk_df = bulk_df.reset_index(drop=False)
bulk_df['bulk'] = f'bulk_{i+1}'
bulk_df['bulk_id'] = bulk_df['bulk'] + '_id_' + bulk_df['index'].astype(str)
bulk_df.set_index('bulk_id', inplace=True)

# Iterate through subsequent bulks and concatenate
for i in tqdm(range(0, 100)):
    df_ = pd.read_csv(path_template.format(i+1))
    df_ = df_.reset_index(drop=False)
    df_['bulk'] = f'bulk_{i+1}'
    df_['bulk_id'] = df_['bulk'] + '_id_' + df_['index'].astype(str)
    df_.set_index('bulk_id', inplace=True)
    bulk_df = pd.concat([bulk_df, df_], axis=0, join='outer')


100%|██████████| 100/100 [00:16<00:00,  6.08it/s]


In [38]:
bulk_df['subclone_bulk'] = (bulk_df['subclone'].astype(str) + '_' + bulk_df['bulk'].astype(str)).astype('category')

In [39]:
# Select all numeric columns except those not to aggregate (like old index)
numeric_cols = bulk_df.select_dtypes(include=['number']).columns.tolist()
if 'index' in numeric_cols:
    numeric_cols.remove('index')

# Group and compute mean for all numeric columns per subclone_bulk
agg_df = bulk_df.groupby('subclone_bulk')[numeric_cols].mean().reset_index()

/var/folders/rk/_8vnc6913c5fyc733rjczgp80000gn/T/ipykernel_3625/4061024358.py:7: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  agg_df = bulk_df.groupby('subclone_bulk')[numeric_cols].mean().reset_index()


In [40]:
# List all gene columns (numeric data only)
gene_cols = [col for col in agg_df.columns if col not in ['subclone_bulk']]

# Library size normalization: scale each row to sum to 1e4 (like sc.pp.normalize_total)
agg_df[gene_cols] = (
    agg_df[gene_cols].div(agg_df[gene_cols].sum(axis=1), axis=0) * 1e4
)

# Log-transform (base 2), similar to sc.pp.log1p
agg_df[gene_cols] = np.log2(agg_df[gene_cols] + 1)


In [41]:
def robust_z_scores(X):
    median = np.median(X, axis=0)
    diff = X - median
    MAD = np.median(np.abs(diff), axis=0)
    z = diff / (MAD * 1.4826 + 1e-8)  # Add epsilon to avoid divide-by-zero
    return z

z = robust_z_scores(agg_df[gene_cols].values)
agg_df[gene_cols] = z


In [42]:
agg_df['subclone'] = agg_df['subclone_bulk'].astype(str).str.split('_bulk').str[0]

/var/folders/rk/_8vnc6913c5fyc733rjczgp80000gn/T/ipykernel_3625/1883174851.py:1: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  agg_df['subclone'] = agg_df['subclone_bulk'].astype(str).str.split('_bulk').str[0]


In [43]:
agg_df

subclone_bulk     22848        14     10058      5825     55347  \
0      1.1.1.1_bulk_1  1.363098 -1.095240 -0.674490 -1.024636  1.211696   
1     1.1.1.1_bulk_10  0.673721 -2.315701 -0.674490 -0.506531  0.739497   
2    1.1.1.1_bulk_100  0.244132 -2.584759 -0.674490 -1.867861 -0.463603   
3     1.1.1.1_bulk_11  0.719264 -2.494986 -0.674490  0.441093 -0.692810   
4     1.1.1.1_bulk_12  0.822159 -1.722498 -0.674490  0.788258  0.403143   
..                ...       ...       ...       ...       ...       ...   
895   healthy_bulk_95 -0.212270  0.641081  0.062728 -0.291753 -0.070962   
896   healthy_bulk_96  0.213338  0.800048  0.272508  0.020297  0.001859   
897   healthy_bulk_97  0.010405 -0.016222  0.231488 -1.150018 -0.417422   
898   healthy_bulk_98 -0.363986  0.287230  0.290965 -1.271090 -0.601254   
899   healthy_bulk_99  0.108574  0.417583  0.111745  0.169951  0.135825   

        25864     51099     57406     10152  ...    125893     55769  \
0   -0.804135  0.718227  0.817064  1.243227  ...  0.156894  3.201645   
1   -0.788710 -0.997278 -0.264447  2.035383  ... -0.421893  2.481156   
2   -0.002185 -0.100892  0.810612  0.732893  ...  0.247715  1.991068   
3   -1.756890  0.673337 -0.252381  2.182951  ...  0.139011  1.788578   
4   -0.614251  1.312182  1.443281  1.693775  ...  1.722156  3.384397   
..        ...       ...       ...       ...  ...       ...       ...   
895  0.130457 -0.562106 -0.463713 -0.129611  ... -0.066473  0.373462   
896  0.547639 -0.498671 -0.672023  0.016514  ... -0.374141  0.163745   
897 -0.096685 -0.229523 -0.630641  0.401655  ... -0.208461 -0.096073   
898  0.035247 -0.196669  0.022458 -0.058789  ... -0.170238  0.364201   
899  0.343465 -0.138218 -0.493056  0.496701  ... -0.051966  0.054998   

         7644     81931      8233     65982     79149     90204    158586  \
0   -0.767380  0.085267 -1.828585  2.122193  2.101359 -0.294057 -1.418737   
1   -0.297210  0.210360 -2.093512  2.464886  0.995436 -0.157073 -1.796231   
2    0.007748 -0.769102 -0.737540  1.792155  1.103662 -0.182433 -2.137007   
3    0.037234  0.302525 -1.240879  2.351110  0.749474  0.135721 -1.852492   
4   -0.196277 -0.792378 -0.989003  3.320654  0.697213  1.253374 -1.941297   
..        ...       ...       ...       ...       ...       ...       ...   
895  0.539888 -0.285333 -0.422760  0.155548  0.087544 -0.930766 -0.304636   
896 -0.295260 -0.005121  0.127486  0.104008 -0.299111 -0.413856 -0.247363   
897  0.195123 -0.098491 -0.617162 -0.339200  0.185858 -0.863546 -0.816509   
898 -0.515062 -0.240288 -0.767822 -0.007760  0.032144 -0.697509 -0.862570   
899 -0.140583  1.205704 -0.170611 -0.155608 -0.943953 -0.475710 -0.407159   

     subclone  
0     1.1.1.1  
1     1.1.1.1  
2     1.1.1.1  
3     1.1.1.1  
4     1.1.1.1  
..        ...  
895   healthy  
896   healthy  
897   healthy  
898   healthy  
899   healthy  

[900 rows x 9610 columns]

In [44]:
df_final_expression = (
    agg_df
    .groupby('subclone')[gene_cols]
    .mean()
    .reset_index()
)

In [45]:
df_final_expression

subclone     22848        14     10058      5825     55347     25864  \
0  1.1.1.1  0.731081 -2.224196 -0.674490  0.123202  0.159591 -0.713548   
1  1.1.1.2 -0.444164  0.506085  0.994845 -0.554687  0.609010  0.969170   
2  1.1.2.1  0.420640 -0.101778 -0.109738  0.186842 -0.286444  0.294771   
3  1.1.2.2 -0.171899  0.355774  0.212865  0.413354 -1.212346  0.591838   
4  1.2.1.1 -0.016504  0.000132 -0.361935  0.680284  0.197888  0.438389   
5  1.2.1.2 -2.495481 -6.560614 -0.674490 -1.429377 -2.734012 -3.719456   
6  1.2.2.1 -1.850646  0.935032  1.501092  0.101407  2.013614 -0.485969   
7  1.2.2.2  1.708724  0.200140  1.365739 -0.252816  1.058746 -0.885648   
8  healthy -0.022126  0.356043  0.222731 -0.150008 -0.037771  0.123140   

      51099     57406     10152  ...    730051    125893     55769      7644  \
0  0.624056  0.362824  1.023604  ... -0.593259 -0.026198  2.141365 -0.360678   
1  0.752708  1.234714  1.247443  ... -0.174323  1.011726 -0.829866 -1.262040   
2 -0.737311  0.092416 -0.394101  ...  0.477981  0.707189 -0.017932  0.104004   
3 -0.338589  0.600921 -0.112383  ... -0.888938  0.091329 -0.754745 -0.580557   
4  0.066851 -0.626892 -0.413503  ... -0.052126  0.785023 -0.388462  0.844744   
5  4.468887  2.231068 -1.883866  ...  0.320532 -0.980024  0.112173  2.082940   
6 -0.687619 -1.946085  2.341447  ... -1.092165 -0.980024  0.260244 -0.619601   
7  0.195835  0.021764 -0.610161  ...  0.880306  0.361767  0.703646  0.719390   
8 -0.621851 -0.209378  0.288227  ...  0.739079 -0.244117  0.372934  0.128973   

      81931      8233     65982     79149     90204    158586  
0  0.164561 -1.642208  1.734473  1.997715  0.500821 -1.699334  
1 -0.304678  0.042154  0.320928 -0.245451 -0.929155 -0.241153  
2  0.469589  0.298256  0.155642  0.081890  0.099296 -0.085902  
3  0.615959 -1.278629 -1.309190  0.765230 -1.036311  1.066614  
4  0.443081  0.321113  0.113969  0.167113  0.310830  0.307660  
5  0.952861  0.167950 -1.952406 -3.750620  7.119967  1.205958  
6 -1.216565  0.752720  1.569709  0.080249  1.167502  1.684870  
7 -1.263067  0.974609 -0.393294 -0.342096  0.003899 -0.222543  
8  0.118720 -0.080879 -0.154830 -0.132512 -0.537780 -0.430179  

[9 rows x 9609 columns]

In [46]:
variants = pd.read_csv('data/aggregated_muts_5.csv')

In [47]:
values_dict = variants.iloc[0].to_dict()
df_final = df_final_expression.assign(**values_dict)

/var/folders/rk/_8vnc6913c5fyc733rjczgp80000gn/T/ipykernel_3625/338592391.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_final = df_final_expression.assign(**values_dict)
/var/folders/rk/_8vnc6913c5fyc733rjczgp80000gn/T/ipykernel_3625/338592391.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_final = df_final_expression.assign(**values_dict)
/var/folders/rk/_8vnc6913c5fyc733rjczgp80000gn/T/ipykernel_3625/338592391.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `fram

In [48]:
df_final

subclone     22848        14     10058      5825     55347     25864  \
0  1.1.1.1  0.731081 -2.224196 -0.674490  0.123202  0.159591 -0.713548   
1  1.1.1.2 -0.444164  0.506085  0.994845 -0.554687  0.609010  0.969170   
2  1.1.2.1  0.420640 -0.101778 -0.109738  0.186842 -0.286444  0.294771   
3  1.1.2.2 -0.171899  0.355774  0.212865  0.413354 -1.212346  0.591838   
4  1.2.1.1 -0.016504  0.000132 -0.361935  0.680284  0.197888  0.438389   
5  1.2.1.2 -2.495481 -6.560614 -0.674490 -1.429377 -2.734012 -3.719456   
6  1.2.2.1 -1.850646  0.935032  1.501092  0.101407  2.013614 -0.485969   
7  1.2.2.2  1.708724  0.200140  1.365739 -0.252816  1.058746 -0.885648   
8  healthy -0.022126  0.356043  0.222731 -0.150008 -0.037771  0.123140   

      51099     57406     10152  ...  ZNF767P  ZNF768  ZNF787  ZNF804A  ZNF83  \
0  0.624056  0.362824  1.023604  ...        2       1       1       48      4   
1  0.752708  1.234714  1.247443  ...        2       1       1       48      4   
2 -0.737311  0.092416 -0.394101  ...        2       1       1       48      4   
3 -0.338589  0.600921 -0.112383  ...        2       1       1       48      4   
4  0.066851 -0.626892 -0.413503  ...        2       1       1       48      4   
5  4.468887  2.231068 -1.883866  ...        2       1       1       48      4   
6 -0.687619 -1.946085  2.341447  ...        2       1       1       48      4   
7  0.195835  0.021764 -0.610161  ...        2       1       1       48      4   
8 -0.621851 -0.209378  0.288227  ...        2       1       1       48      4   

   ZNF84  ZSCAN18  ZXDC  ZYX  ZZEF1  
0      1        1     1    1      1  
1      1        1     1    1      1  
2      1        1     1    1      1  
3      1        1     1    1      1  
4      1        1     1    1      1  
5      1        1     1    1      1  
6      1        1     1    1      1  
7      1        1     1    1      1  
8      1        1     1    1      1  

[9 rows x 13742 columns]

In [49]:
df_final.to_csv('data/gene_expression_processed_pat5.csv', index=False)

In [50]:
tahoe = pd.read_parquet('data/tahoe_formatted_normalized_separate_scaler_for_genes_same_scaler_for_dosage_cellosaurus.parquet')

In [51]:
cols_to_select = ['nearest_dose', 'responses']

# Select all columns starting with 'fps_'
fps_cols = tahoe.filter(regex='^fps_').columns.tolist()

all_cols = [col for col in tahoe.columns if col not in df_final.columns]

# Select these columns from the dataframe, then drop duplicates
df_selected = tahoe[all_cols].drop_duplicates().drop(['sig_id', 'cellosaurus_id'], axis=1)

In [52]:
df_selected

nearest_dose  responses  fps_0  fps_1  fps_2  fps_3  fps_4  fps_5  \
0          0.00025   0.999736      0      0      0      0      0      0   
1          0.00025   0.988290      0      0      0      0      0      0   
2          0.00025   0.786794      0      0      0      0      0      0   
3          0.00025   1.000000      0      1      1      0      0      0   
4          0.00025   0.990883      0      0      0      0      0      0   
...            ...        ...    ...    ...    ...    ...    ...    ...   
3316       0.00250   0.923447      0      0      0      0      0      0   
3317       0.00250   0.912687      0      0      0      0      1      0   
3318       0.00250   0.901148      0      0      0      0      0      0   
3319       0.00250   0.470417      0      0      0      0      0      0   
3320       0.00250   0.499928      0      0      0      0      0      0   

      fps_6  fps_7  ...  WNT3A  FAM98B  MPZL2  RNF14  SAGE2P  SMPD4P2  BTG2  \
0         0      0  ...    1.0     0.0    NaN    NaN     NaN      NaN   0.0   
1         0      0  ...    1.0     0.0    NaN    NaN     NaN      NaN   0.0   
2         0      0  ...    1.0     0.0    NaN    NaN     NaN      NaN   0.0   
3         0      0  ...    1.0     0.0    NaN    NaN     NaN      NaN   0.0   
4         0      0  ...    1.0     0.0    NaN    NaN     NaN      NaN   0.0   
...     ...    ...  ...    ...     ...    ...    ...     ...      ...   ...   
3316      0      0  ...    0.0     0.0    NaN    NaN     NaN      NaN   0.0   
3317      0      0  ...    0.0     0.0    NaN    NaN     NaN      NaN   0.0   
3318      0      0  ...    0.0     0.0    NaN    NaN     NaN      NaN   0.0   
3319      0      0  ...    0.0     0.0    NaN    NaN     NaN      NaN   0.0   
3320      0      0  ...    0.0     0.0    NaN    NaN     NaN      NaN   0.0   

      IGLV3-22  KRTAP4-6  SPSB3  
0          NaN       NaN    NaN  
1          NaN       NaN    NaN  
2          NaN       NaN    NaN  
3          NaN       NaN    NaN  
4          NaN       NaN    NaN  
...        ...       ...    ...  
3316       NaN       NaN    NaN  
3317       NaN       NaN    NaN  
3318       NaN       NaN    NaN  
3319       NaN       NaN    NaN  
3320       NaN       NaN    NaN  

[3321 rows x 17806 columns]

In [53]:
cols = ['nearest_dose', 'responses'] + fps_cols
# Cross join to combine each patient row with each drug-dose pai
expanded_df = df_final.merge(df_selected[cols], how='cross')

In [54]:
expanded_df

subclone     22848        14     10058      5825     55347     25864  \
0      1.1.1.1  0.731081 -2.224196 -0.674490  0.123202  0.159591 -0.713548   
1      1.1.1.1  0.731081 -2.224196 -0.674490  0.123202  0.159591 -0.713548   
2      1.1.1.1  0.731081 -2.224196 -0.674490  0.123202  0.159591 -0.713548   
3      1.1.1.1  0.731081 -2.224196 -0.674490  0.123202  0.159591 -0.713548   
4      1.1.1.1  0.731081 -2.224196 -0.674490  0.123202  0.159591 -0.713548   
...        ...       ...       ...       ...       ...       ...       ...   
29884  healthy -0.022126  0.356043  0.222731 -0.150008 -0.037771  0.123140   
29885  healthy -0.022126  0.356043  0.222731 -0.150008 -0.037771  0.123140   
29886  healthy -0.022126  0.356043  0.222731 -0.150008 -0.037771  0.123140   
29887  healthy -0.022126  0.356043  0.222731 -0.150008 -0.037771  0.123140   
29888  healthy -0.022126  0.356043  0.222731 -0.150008 -0.037771  0.123140   

          51099     57406     10152  ...  fps_2038  fps_2039  fps_2040  \
0      0.624056  0.362824  1.023604  ...         0         0         0   
1      0.624056  0.362824  1.023604  ...         0         0         0   
2      0.624056  0.362824  1.023604  ...         0         0         0   
3      0.624056  0.362824  1.023604  ...         0         0         0   
4      0.624056  0.362824  1.023604  ...         0         0         0   
...         ...       ...       ...  ...       ...       ...       ...   
29884 -0.621851 -0.209378  0.288227  ...         0         0         0   
29885 -0.621851 -0.209378  0.288227  ...         0         0         0   
29886 -0.621851 -0.209378  0.288227  ...         0         0         0   
29887 -0.621851 -0.209378  0.288227  ...         0         0         0   
29888 -0.621851 -0.209378  0.288227  ...         0         0         0   

       fps_2041  fps_2042  fps_2043  fps_2044  fps_2045  fps_2046  fps_2047  
0             0         0         0         0         0         0         0  
1             0         0         0         0         0         1         0  
2             0         0         0         0         0         0         0  
3             0         0         0         0         0         0         0  
4             0         0         0         0         0         0         0  
...         ...       ...       ...       ...       ...       ...       ...  
29884         0         0         0         0         0         0         0  
29885         1         0         0         0         0         0         0  
29886         0         0         0         0         0         0         0  
29887         0         0         0         0         0         0         0  
29888         0         0         0         0         0         1         0  

[29889 rows x 15792 columns]

In [56]:
expanded_df.to_parquet('data/row_to_subclone_pat5.parquet')

In [57]:
missing_cols = [col for col in tahoe.columns if col not in expanded_df.columns]
for col in missing_cols:
    expanded_df[col] = pd.NA

df_ordered = expanded_df[tahoe.columns]

/var/folders/rk/_8vnc6913c5fyc733rjczgp80000gn/T/ipykernel_3625/3202300251.py:3: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  expanded_df[col] = pd.NA
/var/folders/rk/_8vnc6913c5fyc733rjczgp80000gn/T/ipykernel_3625/3202300251.py:3: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  expanded_df[col] = pd.NA
/var/folders/rk/_8vnc6913c5fyc733rjczgp80000gn/T/ipykernel_3625/3202300251.py:3: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Co

In [58]:
df_ordered.drop(columns=['sig_id', 'cellosaurus_id'], inplace=True)

/var/folders/rk/_8vnc6913c5fyc733rjczgp80000gn/T/ipykernel_3625/90282046.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_ordered.drop(columns=['sig_id', 'cellosaurus_id'], inplace=True)


In [59]:
df_ordered

nearest_dose  responses  fps_0  fps_1  fps_2  fps_3  fps_4  fps_5  \
0           0.00025   0.999736      0      0      0      0      0      0   
1           0.00025   0.988290      0      0      0      0      0      0   
2           0.00025   0.786794      0      0      0      0      0      0   
3           0.00025   1.000000      0      1      1      0      0      0   
4           0.00025   0.990883      0      0      0      0      0      0   
...             ...        ...    ...    ...    ...    ...    ...    ...   
29884       0.00250   0.923447      0      0      0      0      0      0   
29885       0.00250   0.912687      0      0      0      0      1      0   
29886       0.00250   0.901148      0      0      0      0      0      0   
29887       0.00250   0.470417      0      0      0      0      0      0   
29888       0.00250   0.499928      0      0      0      0      0      0   

       fps_6  fps_7  ...  MPZL2  RNF14  SAGE2P  SMPD4P2  BTG2  IGLV3-22  \
0          0      0  ...   <NA>   <NA>    <NA>     <NA>  <NA>      <NA>   
1          0      0  ...   <NA>   <NA>    <NA>     <NA>  <NA>      <NA>   
2          0      0  ...   <NA>   <NA>    <NA>     <NA>  <NA>      <NA>   
3          0      0  ...   <NA>   <NA>    <NA>     <NA>  <NA>      <NA>   
4          0      0  ...   <NA>   <NA>    <NA>     <NA>  <NA>      <NA>   
...      ...    ...  ...    ...    ...     ...      ...   ...       ...   
29884      0      0  ...   <NA>   <NA>    <NA>     <NA>  <NA>      <NA>   
29885      0      0  ...   <NA>   <NA>    <NA>     <NA>  <NA>      <NA>   
29886      0      0  ...   <NA>   <NA>    <NA>     <NA>  <NA>      <NA>   
29887      0      0  ...   <NA>   <NA>    <NA>     <NA>  <NA>      <NA>   
29888      0      0  ...   <NA>   <NA>    <NA>     <NA>  <NA>      <NA>   

       KRTAP4-6  PARVB  SPSB3  TAF9B  
0          <NA>      2   <NA>      1  
1          <NA>      2   <NA>      1  
2          <NA>      2   <NA>      1  
3          <NA>      2   <NA>      1  
4          <NA>      2   <NA>      1  
...         ...    ...    ...    ...  
29884      <NA>      2   <NA>      1  
29885      <NA>      2   <NA>      1  
29886      <NA>      2   <NA>      1  
29887      <NA>      2   <NA>      1  
29888      <NA>      2   <NA>      1  

[29889 rows x 31179 columns]

In [61]:
df_ordered.to_parquet('data/pat5_to_predict.parquet')